In [45]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.action_chains import ActionChains
from selenium.webdriver.common.keys import Keys
from selenium.common.exceptions import TimeoutException
from pyquery import PyQuery as pq
from config import *
import pymongo
import re

In [46]:
def search( keyword ):
    try:
        browser.get('https://www.jd.hk/')
        input = wait.until(
            EC.presence_of_element_located((By.CSS_SELECTOR,"#key"))
        )
        submit = wait.until(EC.element_to_be_clickable((By.CSS_SELECTOR,"#search-2014 > div.form > button")))
        input.send_keys(keyword)#搜索 keyword  = "口红"
        submit.click()
        total = wait.until(EC.presence_of_element_located((By.CSS_SELECTOR,"#J_bottomPage > span.p-skip > em:nth-child(1) > b")))#总页数
        return total.text
    except TimeoutException:
        return search()

In [47]:
def next_page(page_number):
    try:
        input = wait.until(
            EC.presence_of_element_located((By.CSS_SELECTOR, "#page_jump_num"))
        )
        input.clear()
        input.send_keys(page_number)
        submit = wait.until(EC.element_to_be_clickable((By.CSS_SELECTOR, "#page_jump_num")))
        submit.send_keys(Keys.ENTER)
        wait.until(EC.text_to_be_present_in_element((By.CSS_SELECTOR,"#J_bottomPage > span.p-num > a.curr"),str(page_number)))
        
        # get the current page info
        get_product()
    except TimeoutException:
        next_page(page_number)

In [48]:
def get_product():
    try:
        print("Ready to get product info:")
        # wait.until(EC.presence_of_element_located((By.CSS_SELECTOR,"#goods-list .gl-warp .gl-item")))
        wait.until(EC.presence_of_element_located((By.CSS_SELECTOR,"#plist > ul > li:nth-child(1)")))
        print("Page loaded successfully")
        html = browser.page_source
        doc = pq(html)
        items = doc(".gl-item").items()

        for item in items:
#             product = {
#                 'product_code':item.find(".price").children().attr("psitemsku"),
#                 'image': item.find(".p-img").children().children().attr("src"),
#                 'price':item.find(".price").text()[2:],
#                 'name': re.sub("\n|全球购","",re.sub(item.find(".name-other").text(),"", item.find(".p-name").text())),
#                 'name-other':item.find('.name-other').text(),
#                 'product_url': item.find('.p-name').children().attr('href'),
#                 'conduct':item.find(".p-conduct").text(),
#                 'comment_num':re.sub("\n条评价","",item.find(".assess").text()),
#                 'shop_name':item.find(".p-shop-name").text(),
#                 'shop_name_url':item.find(".p-shop-name-text").attr("href"),
#                 'shop_chat':item.find(".p-shop-name-icon").attr("href"),
#                 'p-icons':item.find('.p-icons').text()
#             }
            
            product = {
                # remove J_
                'SKU':item.find(".price").children().attr("psitemsku")[2:],
                # unaccessible
                'ImageUrl': item.find(".p-img").children().children().attr("src"),
                'Price':item.find(".price").text()[2:],
                'ProductName': re.sub("\n|全球购","",re.sub(item.find(".name-other").text(),"", item.find(".p-name").text())),
                'NameOther':item.find('.name-other').text(),
                'ProductUrl': item.find('.p-name').children().attr('href'),
                'Conduct':item.find(".p-conduct").text(),
                'CommentNum':re.sub("\n条评价","",item.find(".assess").text()),
                'ShopName':item.find(".p-shop-name").text(),
                'ShopNameUrl':item.find(".p-shop-name-text").attr("href"),
                'ShopChat':item.find(".p-shop-name-icon").attr("href"),
                'Picons':item.find('.p-icons').text()
            }
        
            save_to_mongo(product)
            # save_to_csv(product)
    except TimeoutException:
        return  get_product()

In [49]:
# def save_to_csv(product):

#     with open("product.csv",'w') as f:
#         s=product['image']+','+product['price']+','+product['name']+','+product['product_url']+','+product['conduct']+','+product['comment_num']+','+product['shop_name'] +'\n'
#         try:
#             f.write(s)
#             print('保存到csv成功！',product)
#         except:
#             pass
#数据保存到mongodb中
def save_to_mongo(result):
    
    #global
    global item_count
    item_count += 1
    try:
        if db[MONGO_TABLE].insert(result):
            print('NO:' + str(item_count) +' 插入成功', result)
    except Exception:
        print('NO:' + str(item_count) +' 插入失败', result)


In [50]:
def main():
    try:
        
        keyword = "口红"
        total = int(search(keyword))
        print('Total: ' + str(total) )
        
        for index in range(1,total+1):
            next_page(index)
#         for i in range(1,10):
#             next_page(i)
    except Exception:
        print("出错啦")
    finally:
        browser.close()
        client.close()


In [51]:
#View 
item_count = 0

client = pymongo.MongoClient(MONGO_URL)   # 创建一个连接对象
db = client[MONGO_DB]

MONGO_TABLE = 'lipstick_demo'

options=webdriver.ChromeOptions()
options.add_argument('--ignore-certificate-errors')
browser = webdriver.Chrome(chrome_options=options)
wait = WebDriverWait(browser,10)

C:\Users\Administrator\Anaconda3\lib\site-packages\ipykernel_launcher.py:11: DeprecationWarning: use options instead of chrome_options
  # This is added back by InteractiveShellApp.init_path()


In [52]:
if __name__ == '__main__':
    main()

Total: 157
Ready to get product info:
Page loaded successfully


C:\Users\Administrator\Anaconda3\lib\site-packages\ipykernel_launcher.py:17: DeprecationWarning: insert is deprecated. Use insert_one or insert_many instead.


NO:1 插入成功 {'SKU': '4564204', 'ImageUrl': '//img13.360buyimg.com/n7/jfs/t21946/165/1208592477/32181/1ecee077/5b226dd4N211675fa.jpg!q90', 'Price': '159', 'ProductName': '魅可（MAC)经典唇膏 子弹头口红3g Chili 秀智色/小辣椒色', 'NameOther': '【自营品质】全球美妆尖货部分满199减100，大牌护肤部分2件7折，更有3件5折等！\n》》其他优惠，快来选购', 'ProductUrl': '//item.jd.hk/4564204.html', 'Conduct': '', 'CommentNum': '6.1万+', 'ShopName': 'MAC魅可海外自营专区', 'ShopNameUrl': 'http://mall.jd.hk/index-1000094378.html', 'ShopChat': 'http://chat.jd.com/chat/index.action?venderId=1000094378&entry=sup_web_search', 'Picons': '自营\n包税', '_id': ObjectId('5bac8c2b80692519c029f8a3')}
NO:2 插入成功 {'SKU': '1967134292', 'ImageUrl': '//img13.360buyimg.com/n7/jfs/t1/429/22/9060/336121/5baae852Ecc183e2d/ee1c9d24f1a2271e.jpg!q90', 'Price': '268', 'ProductName': '圣罗兰（YSL）圣罗兰圆管口红唇膏12斩男色46号18年限量新色76号91号92号套装送礼礼盒装 12号 红粉派对 斩男色', 'NameOther': '', 'ProductUrl': '//item.jd.hk/1967134292.html', 'Conduct': '', 'CommentNum': '3.2万+', 'ShopName': '多瑙河之恋全球购旗舰店', 'ShopNameUrl': 'http://mall.jd.hk/

Ready to get product info:
Page loaded successfully
NO:49 插入成功 {'SKU': '1967134295', 'ImageUrl': '//img11.360buyimg.com/n7/jfs/t24670/269/229340166/792399/113136d/5b692259N65e03328.png', 'Price': '293', 'ProductName': '圣罗兰（YSL）圣罗兰圆管口红唇膏12斩男色46号18年限量新色76号91号92号套装送礼礼盒装 14号 一见倾心（珊瑚粉橘色）', 'NameOther': '', 'ProductUrl': '//item.jd.hk/1967134295.html', 'Conduct': '', 'CommentNum': '3.2万+', 'ShopName': '多瑙河之恋全球购旗舰店', 'ShopNameUrl': 'http://mall.jd.hk/index-123541.html', 'ShopChat': 'http://chat.jd.com/chat/index.action?venderId=127110&entry=sup_web_search', 'Picons': '', '_id': ObjectId('5bac8c3380692519c029f8d3')}
NO:50 插入成功 {'SKU': '4350970', 'ImageUrl': '//img13.360buyimg.com/n7/jfs/t17854/166/2633841936/90352/cef782ac/5b04d033Nac84c5b2.jpg!q90', 'Price': '59', 'ProductName': '得鲜（The Saem)按压口红唇膏2g 哑光M05复古红 保湿滋润持久不脱色 韩国原装', 'NameOther': '', 'ProductUrl': '//item.jd.hk/4350970.html', 'Conduct': '', 'CommentNum': '1.1万+', 'ShopName': 'the saem得鲜海外自营旗舰店', 'ShopNameUrl': 'http://mall.jd.hk/inde

Ready to get product info:
Page loaded successfully
NO:97 插入成功 {'SKU': '1967558207', 'ImageUrl': '//img13.360buyimg.com/n7/jfs/t1/4907/39/6617/238754/5ba367f9Ea38159bc/a42c35d269a8eceb.jpg!q90', 'Price': '278', 'ProductName': '香奈儿（Chanel）限定18年新色香奈儿口红58红棕色43珊瑚红57枫叶红62豆沙色184草莓红 热卖58# 红棕色', 'NameOther': '', 'ProductUrl': '//item.jd.hk/1967558207.html', 'Conduct': '', 'CommentNum': '5000+', 'ShopName': '多瑙河之恋全球购旗舰店', 'ShopNameUrl': 'http://mall.jd.hk/index-123541.html', 'ShopChat': 'http://chat.jd.com/chat/index.action?venderId=127110&entry=sup_web_search', 'Picons': '', '_id': ObjectId('5bac8c4680692519c029f903')}
NO:98 插入成功 {'SKU': '1987006630', 'ImageUrl': '//img13.360buyimg.com/n7/jfs/t19258/357/1960575388/109537/1c14cd19/5ae026c2Nafcdf60d.jpg!q90', 'Price': '359', 'ProductName': '汤姆福特（TOM FORD）黑金黑管白管TF口红唇膏 80#IMPASSIONED', 'NameOther': '', 'ProductUrl': '//item.jd.hk/1987006630.html', 'Conduct': '', 'CommentNum': '5100+', 'ShopName': '当然购美妆全球购专营店', 'ShopNameUrl': 'http://mall.jd.hk/in

...

Ready to get product info:
Page loaded successfully
NO:7393 插入成功 {'SKU': '1986985971', 'ImageUrl': '//img10.360buyimg.com/n7/jfs/t18892/49/980867581/277016/501972b0/5ab319a2N6a1c515d.jpg!q90', 'Price': '26', 'ProductName': 'odbo 泰国蜡笔口红持久保湿不脱色防水流苏哑光雾面沙色大红姨妈色唇膏 01#肉色豆沙', 'NameOther': '汇聚全球护肤精品，精选海外好物，关注店铺领取优惠券再下单更优惠→→点击查看', 'ProductUrl': '//item.jd.hk/1986985971.html', 'Conduct': '', 'CommentNum': '50+', 'ShopName': '汇美社海外专营店', 'ShopNameUrl': 'http://mall.jd.hk/index-606050.html', 'ShopChat': 'http://chat.jd.com/chat/index.action?venderId=613343&entry=sup_web_search', 'Picons': '券598-50', '_id': ObjectId('5bac94d280692519c02a1583')}
NO:7394 插入成功 {'SKU': '17875190653', 'ImageUrl': '//img14.360buyimg.com/n7/jfs/t25438/311/217153830/123183/59386b25/5b692c6fNd5cc1f02.jpg!q90', 'Price': '348', 'ProductName': '香奈儿（Chanel） 新年圣诞限量红管口红新款红壳红管丝绒唇膏口红N1N2N3N4 3#', 'NameOther': '', 'ProductUrl': '//item.jd.hk/17875190653.html', 'Conduct': '', 'CommentNum': '100+', 'ShopName': '多瑙河之恋全球购旗舰店', 'ShopNameU

NO:7413 插入成功 {'SKU': '1956937385', 'ImageUrl': '//img11.360buyimg.com/cms/jfs/t2296/67/2540291745/1095/28285fbe/570e2074Nf22696dd.gif', 'Price': '288', 'ProductName': '香奈儿（Chanel） 【下单送礼盒】Chanel香奈儿口红女士丝绒 94#伊恩惠色', 'NameOther': '！！！请付款时自行备注手提袋、包装盒和贺卡，或请客服服务，否则默认不送哦！！！', 'ProductUrl': '//item.jd.hk/1956937385.html', 'Conduct': '', 'CommentNum': '1万+', 'ShopName': '美妍国际专营店', 'ShopNameUrl': 'http://mall.jd.hk/index-193918.html', 'ShopChat': 'http://chat.jd.com/chat/index.action?venderId=202726&entry=sup_web_search', 'Picons': '', '_id': ObjectId('5bac94d280692519c02a1597')}
NO:7414 插入成功 {'SKU': '1967745187', 'ImageUrl': '//img11.360buyimg.com/cms/jfs/t2296/67/2540291745/1095/28285fbe/570e2074Nf22696dd.gif', 'Price': '57', 'ProductName': 'KIKO 意大利口红唇膏SMART LIPSTICK丰盈润泽9系 持久不掉色 907#橘色 发新款413#', 'NameOther': '', 'ProductUrl': '//item.jd.hk/1967745187.html', 'Conduct': '', 'CommentNum': '400+', 'ShopName': '珍妮轩全球购专营店', 'ShopNameUrl': 'http://mall.jd.hk/index-191504.html', 'ShopChat': 'http://ch

Ready to get product info:
Page loaded successfully
NO:7441 插入成功 {'SKU': '26685301586', 'ImageUrl': '//img12.360buyimg.com/n7/jfs/t1/1365/29/8668/178456/5baa1405E5c8604ad/934e192259034856.jpg!q90', 'Price': '39', 'ProductName': 'e.l.f. 红糖唇部磨砂膏 4.5g 持久不脱妆', 'NameOther': '周年庆狂欢 50元券限量抢，秒杀低至9.9元，满减低至满399减175，\n更多优惠点击查看', 'ProductUrl': '//item.jd.hk/26685301586.html', 'Conduct': '', 'CommentNum': '100+', 'ShopName': '沃尔玛全球购官方旗舰店', 'ShopNameUrl': 'http://mall.jd.hk/index-597359.html', 'ShopChat': 'http://chat.jd.com/chat/index.action?venderId=604706&entry=sup_web_search', 'Picons': '京东物流', '_id': ObjectId('5bac94e880692519c02a15b3')}
NO:7442 插入成功 {'SKU': '1974576954', 'ImageUrl': '//img11.360buyimg.com/n7/jfs/t12898/364/2438974632/153252/3116936/5a45b968N7eab5777.jpg!q90', 'Price': '29', 'ProductName': "小蜜蜂（Burt's Bees） 美国润唇膏 保湿防干裂孕妇润唇膏女 婴儿童宝宝护唇膏 新品草莓 清新酸甜", 'NameOther': '【品牌授权直营】免邮】组合装购买更划算 天然唇膏 孕妇可用 更多好礼优惠等你来享', 'ProductUrl': '//item.jd.hk/1974576954.html', 'Conduct': '', 'CommentNum': '2

NO:7470 插入成功 {'SKU': '1983947193', 'ImageUrl': '//img11.360buyimg.com/cms/jfs/t2296/67/2540291745/1095/28285fbe/570e2074Nf22696dd.gif', 'Price': '49.90', 'ProductName': '得鲜（the saem）口红爱可按压口红润唇膏姨妈色咬唇妆不易掉色女 哑光M08铁锈红色', 'NameOther': '【香港直邮，正品保障，pick好物】\n更多优惠点我抢购！！！新一季“妆女郎”就是你！', 'ProductUrl': '//item.jd.hk/1983947193.html', 'Conduct': '', 'CommentNum': '20+', 'ShopName': 'Miss Sugar全球购旗舰店', 'ShopNameUrl': 'http://mall.jd.hk/index-591919.html', 'ShopChat': 'http://chat.jd.com/chat/index.action?venderId=600049&entry=sup_web_search', 'Picons': '', '_id': ObjectId('5bac94e880692519c02a15d0')}
NO:7471 插入成功 {'SKU': '1985286053', 'ImageUrl': '//img11.360buyimg.com/cms/jfs/t2296/67/2540291745/1095/28285fbe/570e2074Nf22696dd.gif', 'Price': '39.90', 'ProductName': '谜尚（Missha） MISSHA minions谜尚 小黄人限量蜡笔气垫口红唇膏 RD01 樱桃红', 'NameOther': '', 'ProductUrl': '//item.jd.hk/1985286053.html', 'Conduct': '', 'CommentNum': '30+', 'ShopName': 'Foreign Experience 全球购官方旗舰店', 'ShopNameUrl': 'http://mall.jd.hk/index-59

Ready to get product info:
Page loaded successfully
NO:7489 插入成功 {'SKU': '24815990217', 'ImageUrl': '//img11.360buyimg.com/n7/jfs/t18001/185/1604201714/86623/c3b35168/5ad175e0Nfb6b019d.jpg!q90', 'Price': '780', 'ProductName': '芦丹氏（SergeLutens） 芦丹氏唇膏口红2.3g修护唇纹 持久滋润显色 多新色 #6MAUVE-DE-SWAN', 'NameOther': '下单满399减10/599减20/1599减100', 'ProductUrl': '//item.jd.hk/24815990217.html', 'Conduct': '', 'CommentNum': '10+', 'ShopName': '华婷国际专营店', 'ShopNameUrl': 'http://mall.jd.hk/index-612131.html', 'ShopChat': 'http://chat.jd.com/chat/index.action?venderId=619531&entry=sup_web_search', 'Picons': '券399-10', '_id': ObjectId('5bac94f480692519c02a15e3')}
NO:7490 插入成功 {'SKU': '24815990219', 'ImageUrl': '//img12.360buyimg.com/n7/jfs/t18130/83/1619403390/90921/84f7c10a/5ad175ecN83e695d9.jpg!q90', 'Price': '780', 'ProductName': '芦丹氏（SergeLutens） 芦丹氏唇膏口红2.3g修护唇纹 持久滋润显色 多新色 #8COMPLIMENT-BEIGE', 'NameOther': '下单满399减10/599减20/1599减100', 'ProductUrl': '//item.jd.hk/24815990219.html', 'Conduct': '', 'CommentNum